In [108]:
import pandas as pd

In [110]:
df = pd.read_csv('../../lol_data/matchinfo.csv')
df.head(3)

League  Year  Season    Type blueTeamTag  bResult  rResult redTeamTag  \
0  NALCS  2015  Spring  Season         TSM        1        0         C9   
1  NALCS  2015  Spring  Season         CST        0        1        DIG   
2  NALCS  2015  Spring  Season         WFX        1        0         GV   

   gamelength  blueTop  ... redTopChamp     redJungle redJungleChamp  \
0          40    Dyrus  ...        Gnar        Meteos          Elise   
1          38     Cris  ...      Irelia       Crumbzz       JarvanIV   
2          40  Flaresz  ...        Sion  Saintvicious         LeeSin   

  redMiddle redMiddleChamp  redADC redADCChamp   redSupport redSupportChamp  \
0       Hai           Fizz  Sneaky       Sivir  LemonNation          Thresh   
1  Shiphtur           Azir  CoreJJ       Corki      KiWiKiD           Annie   
2     Keane           Azir     Cop       Corki   BunnyFuFuu           Janna   

                                             Address  
0  http://matchhistory.na.leagueoflegends.com/en/...  
1  http://matchhistory.na.leagueoflegends.com/en/...  
2  http://matchhistory.na.leagueoflegends.com/en/...  

[3 rows x 30 columns]

In [124]:
teams = set(list(df['blueTeamTag'].unique()) + list(df['redTeamTag'].unique()))
len(teams)

247

In [142]:
cleaned_df = df[(df['blueTeamTag'].isnull() == False) & (df['redTeamTag'].isnull() == False)]
cleaned_df.count()

League              7582
Year                7582
Season              7582
Type                7582
blueTeamTag         7582
bResult             7582
rResult             7582
redTeamTag          7582
gamelength          7582
blueTop             7582
blueTopChamp        7582
blueJungle          7582
blueJungleChamp     7582
blueMiddle          7582
blueMiddleChamp     7582
blueADC             7582
blueADCChamp        7582
blueSupport         7582
blueSupportChamp    7582
redTop              7582
redTopChamp         7582
redJungle           7582
redJungleChamp      7582
redMiddle           7582
redMiddleChamp      7582
redADC              7582
redADCChamp         7582
redSupport          7582
redSupportChamp     7582
Address             7582
dtype: int64

In [6]:
test = cleaned_df.sample(frac=0.1, random_state=3)
train = cleaned_df.drop(test.index)

In [8]:
from sklearn.impute import KNNImputer

In [9]:
imputer = KNNImputer(n_neighbors=5)

In [12]:
factorized_cols = {}

In [14]:
test = test.drop(['index', 'League', 'Year', 'Season', 'Type', 'Address', 'Unnamed: 31', 'gamelength'], axis=1)
need_factorizing = list(test.columns)

In [16]:
need_factorizing.pop(1)
need_factorizing.pop(1)
need_factorizing

['blueTeamTag',
 'redTeamTag',
 'blueTop',
 'blueTopChamp',
 'blueJungle',
 'blueJungleChamp',
 'blueMiddle',
 'blueMiddleChamp',
 'blueADC',
 'blueADCChamp',
 'blueSupport',
 'blueSupportChamp',
 'redTop',
 'redTopChamp',
 'redJungle',
 'redJungleChamp',
 'redMiddle',
 'redMiddleChamp',
 'redADC',
 'redADCChamp',
 'redSupport',
 'redSupportChamp']

In [18]:
test_imputation_index = {}
for col in need_factorizing:
    factorization = pd.factorize(test[col])
    factorized_cols[col] = factorization[0]
    test_imputation_index[col] = list(factorization[1])

In [20]:
factorized_test = test[['bResult', 'rResult']].copy(deep=True)
factorized_test.head(3)

bResult  rResult
1041        1        0
3350        0        1
7576        0        1

In [22]:
for col in need_factorizing:
    col_name = 'factorized_' + col
    factorized_test[col_name] = factorized_cols[col]
factorized_test.head(3)

bResult  rResult  factorized_blueTeamTag  factorized_redTeamTag  \
1041        1        0                       0                      0   
3350        0        1                       1                      1   
7576        0        1                       2                      2   

      factorized_blueTop  factorized_blueTopChamp  factorized_blueJungle  \
1041                   0                        0                      0   
3350                   1                        1                      1   
7576                   2                        2                      2   

      factorized_blueJungleChamp  factorized_blueMiddle  \
1041                           0                      0   
3350                           1                      1   
7576                           2                      2   

      factorized_blueMiddleChamp  ...  factorized_redTop  \
1041                           0  ...                  0   
3350                           0  ...                  1   
7576                           1  ...                  2   

      factorized_redTopChamp  factorized_redJungle  factorized_redJungleChamp  \
1041                       0                     0                          0   
3350                       1                     1                          1   
7576                       2                     2                          2   

      factorized_redMiddle  factorized_redMiddleChamp  factorized_redADC  \
1041                     0                          0                  0   
3350                     1                          1                  1   
7576                     2                          2                  2   

      factorized_redADCChamp  factorized_redSupport  \
1041                       0                      0   
3350                       1                      1   
7576                       2                      2   

      factorized_redSupportChamp  
1041                           0  
3350                           1  
7576                           2  

[3 rows x 24 columns]

In [24]:
factorized_cols_train = {}

In [26]:
train = train.drop(['index', 'League', 'Year', 'Season', 'Type', 'Address', 'Unnamed: 31', 'gamelength'], axis=1)
train_imputation_index = {}
for col in need_factorizing:
    factorization = pd.factorize(train[col])
    factorized_cols_train[col] = factorization[0]
    train_imputation_index[col] = list(factorization[1])
factorized_train = train[['bResult', 'rResult']].copy(deep=True)
for col in need_factorizing:
    col_name = 'factorized_' + col
    factorized_train[col_name] = factorized_cols_train[col]
factorized_train.head(3)

bResult  rResult  factorized_blueTeamTag  factorized_redTeamTag  \
0        1        0                       0                      0   
1        0        1                       1                      1   
2        1        0                       2                      2   

   factorized_blueTop  factorized_blueTopChamp  factorized_blueJungle  \
0                   0                        0                      0   
1                   1                        1                      1   
2                   2                        2                      2   

   factorized_blueJungleChamp  factorized_blueMiddle  \
0                           0                      0   
1                           1                      1   
2                           1                      2   

   factorized_blueMiddleChamp  ...  factorized_redTop  factorized_redTopChamp  \
0                           0  ...                  0                       0   
1                           0  ...                  1                       1   
2                           1  ...                  2                       2   

   factorized_redJungle  factorized_redJungleChamp  factorized_redMiddle  \
0                     0                          0                     0   
1                     1                          1                     1   
2                     2                          2                     2   

   factorized_redMiddleChamp  factorized_redADC  factorized_redADCChamp  \
0                          0                  0                       0   
1                          1                  1                       1   
2                          1                  2                       1   

   factorized_redSupport  factorized_redSupportChamp  
0                      0                           0  
1                      1                           1  
2                      2                           2  

[3 rows x 24 columns]

In [28]:
imputed_test = imputer.fit_transform(factorized_test)
imputed_train = imputer.fit_transform(factorized_train)

In [30]:
# start here
train_df = pd.DataFrame(data=imputed_train, columns=list(factorized_train.columns))
train_df.tail(3)

bResult  rResult  factorized_blueTeamTag  factorized_redTeamTag  \
6821      0.0      1.0                   122.0                  118.0   
6822      1.0      0.0                   121.0                  190.0   
6823      0.0      1.0                   190.0                  121.0   

      factorized_blueTop  factorized_blueTopChamp  factorized_blueJungle  \
6821               185.0                     40.0                  202.0   
6822               188.0                     74.0                  200.0   
6823               272.0                     33.0                  306.0   

      factorized_blueJungleChamp  factorized_blueMiddle  \
6821                         2.0                  274.0   
6822                        18.0                  181.0   
6823                         9.0                  187.0   

      factorized_blueMiddleChamp  ...  factorized_redTop  \
6821                        16.0  ...              175.0   
6822                         5.0  ...              277.0   
6823                        16.0  ...              191.0   

      factorized_redTopChamp  factorized_redJungle  factorized_redJungleChamp  \
6821                    26.0                 304.0                       12.0   
6822                    26.0                 305.0                        1.0   
6823                    77.0                 198.0                        1.0   

      factorized_redMiddle  factorized_redMiddleChamp  factorized_redADC  \
6821                 178.0                       44.0              171.0   
6822                 191.0                       58.0              189.0   
6823                 184.0                       44.0              180.0   

      factorized_redADCChamp  factorized_redSupport  \
6821                     5.0                  199.0   
6822                     0.0                  202.0   
6823                    11.0                  204.0   

      factorized_redSupportChamp  
6821                        20.0  
6822                         2.0  
6823                         7.0  

[3 rows x 24 columns]

In [32]:
col_types = {}
for col in list(train_df.columns):
    col_types[col] = 'object'
train_df = train_df.astype(col_types)
train_df.dtypes

bResult                        object
rResult                        object
factorized_blueTeamTag         object
factorized_redTeamTag          object
factorized_blueTop             object
factorized_blueTopChamp        object
factorized_blueJungle          object
factorized_blueJungleChamp     object
factorized_blueMiddle          object
factorized_blueMiddleChamp     object
factorized_blueADC             object
factorized_blueADCChamp        object
factorized_blueSupport         object
factorized_blueSupportChamp    object
factorized_redTop              object
factorized_redTopChamp         object
factorized_redJungle           object
factorized_redJungleChamp      object
factorized_redMiddle           object
factorized_redMiddleChamp      object
factorized_redADC              object
factorized_redADCChamp         object
factorized_redSupport          object
factorized_redSupportChamp     object
dtype: object

In [34]:
for col in list(train_df.columns):
    col_name = col[11:]
    if col_name in train_imputation_index.keys():
        for index in range(len(train_imputation_index[col_name])):
            replacement_val = train_imputation_index[col_name][index]
            train_df.loc[train_df[col] == index, col] = replacement_val

In [35]:
def switch(result_val):
    if result_val == 1:
        return 0
    else:
        return 1

In [36]:
def createPlayerRole(col_name, col_alt, player, b_win):
    matches = len(list(train_df[train_df[col_name] == player][col_name]))
    matches += len(list(train_df[train_df[col_alt] == player][col_alt]))
    wins = len(list(train_df[(train_df[col_name] == player) & (train_df['bResult'] == b_win)][col_name]))
    wins += len(list(train_df[(train_df[col_alt] == player) & (train_df['bResult'] == switch(b_win))][col_alt]))
    if matches == 0:
        return 0.5
    else:
        return wins / matches

In [37]:
def createCoopPlayers(players, blue_cols, red_cols, b_win):
    total = 0
    for i in range(len(players)):
        sub_total = 0
        df_blue = train_df[(train_df[blue_cols[0]] == players[i]) | (train_df[blue_cols[1]] == players[i]) | \
        (train_df[blue_cols[2]] == players[i]) | (train_df[blue_cols[3]] == players[i]) | \
        (train_df[blue_cols[4]] == players[i])]
        df_red = train_df[(train_df[red_cols[0]] == players[i]) | (train_df[red_cols[1]] == players[i]) | \
        (train_df[red_cols[2]] == players[i]) | (train_df[red_cols[3]] == players[i]) | \
        (train_df[red_cols[4]] == players[i])]
        for j in range(len(players)):
            if i != j:
                # matches = len(list(train_df[(train_df[color_cols[i]] == players[i]) & (train_df[color_cols[j] == players[j])]))
                # wins = len(list(train_df[(train_df[color_cols[i]] == players[i]) & (train_df[color_cols[j] == players[j]) & \
                #                 (train_df['bResult'] == b_win)]))
                # ratio = wins / matches
                # sub_total += ratio
                matches = len(df_blue[(df_blue[blue_cols[0]] == players[j]) | (df_blue[blue_cols[1]] == players[j]) | \
                (df_blue[blue_cols[2]] == players[j]) | (df_blue[blue_cols[3]] == players[j]) | \
                (df_blue[blue_cols[4]] == players[j])])
                
                matches += len(df_red[(df_red[red_cols[0]] == players[j]) | (df_red[red_cols[1]] == players[j]) | \
                (df_red[red_cols[2]] == players[j]) | (df_red[red_cols[3]] == players[j]) | \
                (df_red[red_cols[4]] == players[j])])
                
                wins = len(df_blue[((df_blue[blue_cols[0]] == players[j]) | (df_blue[blue_cols[1]] == players[j]) | \
                (df_blue[blue_cols[2]] == players[j]) | (df_blue[blue_cols[3]] == players[j]) | \
                (df_blue[blue_cols[4]] == players[j])) & (df_blue['bResult'] == 1)])
                
                wins += len(df_red[((df_red[red_cols[0]] == players[j]) | (df_red[red_cols[1]] == players[j]) | \
                (df_red[red_cols[2]] == players[j]) | (df_red[red_cols[3]] == players[j]) | \
                (df_red[red_cols[4]] == players[j])) & (df_red['bResult'] == 0)])
                ratio = 0
                if matches == 0:
                    ratio += 0.5
                else:
                    ratio += wins / matches
                sub_total += ratio
        total += sub_total
    return total

In [38]:
def createVSPlayer(blue_players, red_players, blue_cols, red_cols):
    total = 0
    for bp in blue_players:
        sub_total = 0
        df_blue = train_df[(train_df[blue_cols[0]] == bp) | (train_df[blue_cols[1]] == bp) | \
        (train_df[blue_cols[2]] == bp) | (train_df[blue_cols[3]] == bp) | \
        (train_df[blue_cols[4]] == bp)]
        df_red = train_df[(train_df[red_cols[0]] == bp) | (train_df[red_cols[1]] == bp) | \
        (train_df[red_cols[2]] == bp) | (train_df[red_cols[3]] == bp) | \
        (train_df[red_cols[4]] == bp)]
        for rp in red_players:
            matches = len(df_blue[(df_blue[red_cols[0]] == bp) | (df_blue[red_cols[1]] == rp) | \
                (df_blue[red_cols[2]] == rp) | (df_blue[red_cols[3]] == rp) | \
                (df_blue[red_cols[4]] == rp)])
            matches += len(df_red[(df_red[blue_cols[0]] == rp) | (df_red[blue_cols[1]] == rp) | \
                (df_red[blue_cols[2]] == rp) | (df_red[blue_cols[3]] == rp) | \
                (df_red[blue_cols[4]] == rp)])
            wins = len(df_blue[((df_blue[red_cols[0]] == rp) | (df_blue[red_cols[1]] == rp) | \
                (df_blue[red_cols[2]] == rp) | (df_blue[red_cols[3]] == rp) | \
                (df_blue[red_cols[4]] == rp)) & (df_blue['bResult'] == 1)])
            wins += len(df_red[((df_red[blue_cols[0]] == rp) | (df_red[blue_cols[1]] == rp) | \
                (df_red[blue_cols[2]] == rp) | (df_red[blue_cols[3]] == rp) | \
                (df_red[blue_cols[4]] == rp)) & (df_red['bResult'] == 0)])
            ratio = 0
            if matches == 0:
                ratio += 0.5
            else:
                ratio += wins / matches
            sub_total += ratio
        total += sub_total
    return total

In [44]:
def createTeamColor(team_tag):
    matches = len(train_df[train_df['factorized_blueTeamTag'] == team_tag])
    matches += len(train_df[train_df['factorized_redTeamTag'] == team_tag])
    
    wins = len(train_df[(train_df['factorized_blueTeamTag'] == team_tag) & (train_df['bResult'] == 1)])
    wins += len(train_df[(train_df['factorized_redTeamTag'] == team_tag) & (train_df['bResult'] == 0)])
    
    if matches == 0:
        return 0.5
    else:
        return wins / matches

In [46]:
player_roles = {
    'top': ['factorized_blueTop', 'factorized_redTop'],
    'jungle': ['factorized_blueJungle', 'factorized_redJungle'],
    'middle': ['factorized_blueMiddle', 'factorized_redMiddle'],
    'adc': ['factorized_blueADC', 'factorized_redADC'],
    'support': ['factorized_blueSupport', 'factorized_redSupport']
}

In [48]:
champ_roles = {
    'top': ['factorized_blueTopChamp', 'factorized_redTopChamp'],
    'jungle': ['factorized_blueJungleChamp', 'factorized_redJungleChamp'],
    'middle': ['factorized_blueMiddleChamp', 'factorized_redMiddleChamp'],
    'adc': ['factorized_blueADCChamp', 'factorized_redADCChamp'],
    'support': ['factorized_blueSupportChamp', 'factorized_redSupportChamp']
}

In [58]:
new_cols = ['bResult', 'btPlayerRole', 'bjPlayerRole', 'bmPlayerRole', 'baPlayerRole', 'bsPlayerRole', 'rtPlayerRole',\
            'rjPlayerRole', 'rmPlayerRole', 'raPlayerRole', 'rsPlayerRole', 'btPlayerChampion', 'bjPlayerChampion',\
            'bmPlayerChampion', 'baPlayerChampion', 'bsPlayerChampion', 'rtPlayerChampion', 'rjPlayerChampion',\
            'rmPlayerChampion', 'raPlayerChampion', 'rsPlayerChampion', 'bCoopPlayer', 'rCoopPlayer', 'bCoopChampion',\
            'rCoopChampion', 'vsPlayer', 'vsChampion', 'bTeamColor', 'rTeamColor']
final_train = pd.DataFrame(data=[[0, 0, 0, 0, 0, 0, \
                                 0, 0, 0, 0, 0, 0, \
                                 0, 0, 0, 0, 0, \
                                 0, 0, 0, 0, 0, 0, \
                                 0, 0, 0, 0, 0, 0]], columns=new_cols)
final_train

bResult  btPlayerRole  bjPlayerRole  bmPlayerRole  baPlayerRole  \
0        0             0             0             0             0   

   bsPlayerRole  rtPlayerRole  rjPlayerRole  rmPlayerRole  raPlayerRole  ...  \
0             0             0             0             0             0  ...   

   raPlayerChampion  rsPlayerChampion  bCoopPlayer  rCoopPlayer  \
0                 0                 0            0            0   

   bCoopChampion  rCoopChampion  vsPlayer  vsChampion  bTeamColor  rTeamColor  
0              0              0         0           0           0           0  

[1 rows x 29 columns]

In [60]:
for index, row in train_df.iterrows():
# btPlayerRole
    bt_player = row['factorized_blueTop']
    bt_player_role = createPlayerRole(player_roles['top'][0], player_roles['top'][1], bt_player, 1)
# bjPlayerRole
    bj_player = row['factorized_blueJungle']
    bj_player_role = createPlayerRole(player_roles['jungle'][0], player_roles['jungle'][1], bj_player, 1)
# bmPlayerRole
    bm_player = row['factorized_blueMiddle']
    bm_player_role = createPlayerRole(player_roles['middle'][0], player_roles['middle'][1], bm_player, 1)
# baPlayerRole
    ba_player = row['factorized_blueADC']
    ba_player_role = createPlayerRole(player_roles['adc'][0], player_roles['adc'][1], ba_player, 1)
# bsPlayerRole
    bs_player = row['factorized_blueSupport']
    bs_player_role = createPlayerRole(player_roles['support'][0], player_roles['support'][1], bs_player, 1)
# rtPlayerRole
    rt_player = row['factorized_redTop']
    rt_player_role = createPlayerRole(player_roles['top'][1], player_roles['top'][0], rt_player, 0)
# rjPlayerRole
    rj_player = row['factorized_redJungle']
    rj_player_role = createPlayerRole(player_roles['jungle'][1], player_roles['jungle'][0], rj_player, 0)
# rmPlayerRole
    rm_player = row['factorized_redMiddle']
    rm_player_role = createPlayerRole(player_roles['middle'][1], player_roles['middle'][0], rm_player, 0)
# raPlayerRole
    ra_player = row['factorized_redADC']
    ra_player_role = createPlayerRole(player_roles['adc'][1], player_roles['adc'][0], ra_player, 0)
# rsPlayerRole
    rs_player = row['factorized_redSupport']
    rs_player_role = createPlayerRole(player_roles['support'][1], player_roles['support'][0], rs_player, 0)
# btPlayerChampion
    bt_champ = row['factorized_blueTopChamp']
    bt_player_champion = createPlayerRole(champ_roles['top'][0], champ_roles['top'][1], bt_champ, 1)
# bjPlayerChampion
    bj_champ = row['factorized_blueJungleChamp']
    bj_player_champion = createPlayerRole(champ_roles['jungle'][0], champ_roles['jungle'][1], bj_champ, 1)
# bmPlayerChampion
    bm_champ = row['factorized_blueMiddleChamp']
    bm_player_champion = createPlayerRole(champ_roles['middle'][0], champ_roles['middle'][1], bm_champ, 1)
# baPlayerChampion
    ba_champ = row['factorized_blueADCChamp']
    ba_player_champion = createPlayerRole(champ_roles['adc'][0], champ_roles['adc'][1], ba_champ, 1)
# bsPlayerChampion
    bs_champ = row['factorized_blueSupportChamp']
    bs_player_champion = createPlayerRole(champ_roles['support'][0], champ_roles['support'][1], bs_champ, 1)
# rtPlayerChampion
    rt_champ = row['factorized_redTopChamp']
    rt_player_champion = createPlayerRole(champ_roles['top'][1], champ_roles['top'][0], rt_champ, 0)
# rjPlayerChampion
    rj_champ = row['factorized_redJungleChamp']
    rj_player_champion = createPlayerRole(champ_roles['jungle'][1], champ_roles['jungle'][0], rj_champ, 0)
# rmPlayerChampion
    rm_champ = row['factorized_redMiddleChamp']
    rm_player_champion = createPlayerRole(champ_roles['middle'][1], champ_roles['middle'][0], rm_champ, 0)
# raPlayerChampion
    ra_champ = row['factorized_redADCChamp']
    ra_player_champion = createPlayerRole(champ_roles['adc'][1], champ_roles['adc'][0], ra_champ, 0)
# rsPlayerChampion
    rs_champ = row['factorized_redSupportChamp']
    rs_player_champion = createPlayerRole(champ_roles['support'][1], champ_roles['support'][0], rs_champ, 0)
# bCoopPlayer
    blue_players = [bt_player, bj_player, bm_player, ba_player, bs_player]
    blue_cols = ['factorized_blueTop', 'factorized_blueJungle', 'factorized_blueMiddle', 'factorized_blueADC', 'factorized_blueSupport']
    red_cols = ['factorized_redTop', 'factorized_redJungle', 'factorized_redMiddle', 'factorized_redADC', 'factorized_redSupport']
    b_coop_player = createCoopPlayers(blue_players, blue_cols, red_cols, 1)
# rCoopPlayer
    red_players = [rt_player, rj_player, rm_player, ra_player, rs_player]
    r_coop_player = createCoopPlayers(red_players, blue_cols, red_cols, 0)
# bCoopChampion
    blue_champs = [bt_champ, bj_champ, bm_champ, ba_champ, bs_champ]
    blue_champ_cols = ['factorized_blueTopChamp', 'factorized_blueJungleChamp', 'factorized_blueMiddleChamp', 'factorized_blueADCChamp', \
                 'factorized_blueSupportChamp']
    red_champ_cols = ['factorized_redTopChamp', 'factorized_redJungleChamp', 'factorized_redMiddleChamp', 'factorized_redADCChamp', \
                 'factorized_redSupportChamp']
    b_coop_champion = createCoopPlayers(blue_champs, blue_champ_cols, red_champ_cols, 1)
# rCoopChampion
    red_champs = [rt_champ, rj_champ, rm_champ, ra_champ, rs_champ]
    r_coop_champion = createCoopPlayers(red_champs, blue_champ_cols, red_champ_cols, 0)
# vsPlayer
    vs_player = createVSPlayer(blue_players, red_players, blue_cols, red_cols)
# vsChampion
    vs_champion = createVSPlayer(blue_champs, red_champs, blue_champ_cols, red_champ_cols)
# bTeamColor
    # b_team_color = createTeamColor(blue_players + blue_champs, blue_cols + blue_champ_cols, 1)
    b_team_tag = row['factorized_blueTeamTag']
    b_team_color = createTeamColor(b_team_tag)
# rTeamColor
    # r_team_color = createTeamColor(red_players + red_champs, red_cols + red_champ_cols, 0)
    r_team_tag = row['factorized_redTeamTag']
    r_team_color = createTeamColor(r_team_tag)
    new_col_values = [row['bResult'], bt_player_role, bj_player_role, bm_player_role, ba_player_role, bs_player_role, \
                     rt_player_role, rj_player_role, rm_player_role, ra_player_role, rs_player_role, \
                     bt_player_champion, bj_player_champion, bm_player_champion, ba_player_champion, bs_player_champion, \
                     rt_player_champion, rj_player_champion, rm_player_champion, ra_player_champion, rs_player_champion, \
                     b_coop_player, r_coop_player, b_coop_champion, r_coop_champion, vs_player, vs_champion, b_team_color, \
                     r_team_color]
    new_row = {}
    for new_col in range(len(new_col_values)):
        new_row[new_cols[new_col]] = new_col_values[new_col]
    print(new_row)
    final_train = final_train._append(new_row, ignore_index=True)

{'bResult': 1.0, 'btPlayerRole': 0.6052631578947368, 'bjPlayerRole': 0.47058823529411764, 'bmPlayerRole': 0.6470588235294118, 'baPlayerRole': 0.606425702811245, 'bsPlayerRole': 0.6052631578947368, 'rtPlayerRole': 0.49743589743589745, 'rjPlayerRole': 0.5588235294117647, 'rmPlayerRole': 0.4825174825174825, 'raPlayerRole': 0.5681818181818182, 'rsPlayerRole': 0.48314606741573035, 'btPlayerChampion': 0.4935400516795866, 'bjPlayerChampion': 0.4899951195705222, 'bmPlayerChampion': 0.49516129032258066, 'baPlayerChampion': 0.45739910313901344, 'bsPlayerChampion': 0.5338441890166028, 'rtPlayerChampion': 0.504424778761062, 'rjPlayerChampion': 0.5065005417118094, 'rmPlayerChampion': 0.5486725663716814, 'raPlayerChampion': 0.5320427236315087, 'rsPlayerChampion': 0.5280184864240324, 'bCoopPlayer': 12.022352811773114, 'rCoopPlayer': 10.44897048034177, 'bCoopChampion': 9.619471415828157, 'rCoopChampion': 11.370756877648581, 'vsPlayer': 17.973818233000152, 'vsChampion': 15.762498496624751, 'bTeamColor'

In [62]:
final_train.head(3)

bResult  btPlayerRole  bjPlayerRole  bmPlayerRole  baPlayerRole  \
0      0.0      0.000000      0.000000      0.000000      0.000000   
1      1.0      0.605263      0.470588      0.647059      0.606426   
2      0.0      0.468085      0.428571      0.500000      0.394737   

   bsPlayerRole  rtPlayerRole  rjPlayerRole  rmPlayerRole  raPlayerRole  ...  \
0      0.000000      0.000000      0.000000      0.000000      0.000000  ...   
1      0.605263      0.497436      0.558824      0.482517      0.568182  ...   
2      0.400000      0.490000      0.250000      0.350000      0.461538  ...   

   raPlayerChampion  rsPlayerChampion  bCoopPlayer  rCoopPlayer  \
0          0.000000          0.000000     0.000000     0.000000   
1          0.532043          0.528018    12.022353    10.448970   
2          0.495007          0.533597     9.449351     7.197822   

   bCoopChampion  rCoopChampion   vsPlayer  vsChampion  bTeamColor  rTeamColor  
0       0.000000       0.000000   0.000000    0.000000    0.000000    0.000000  
1       9.619471      11.370757  17.973818   15.762498    0.647059    0.568182  
2       8.599307      10.328071   2.111111   14.630073    0.405405    0.433962  

[3 rows x 29 columns]

In [64]:
# drop the first row
final_train = final_train.drop(0)
final_train.head(3)

bResult  btPlayerRole  bjPlayerRole  bmPlayerRole  baPlayerRole  \
1      1.0      0.605263      0.470588      0.647059      0.606426   
2      0.0      0.468085      0.428571      0.500000      0.394737   
3      1.0      0.385714      0.500000      0.608889      0.500000   

   bsPlayerRole  rtPlayerRole  rjPlayerRole  rmPlayerRole  raPlayerRole  ...  \
1      0.605263      0.497436      0.558824      0.482517      0.568182  ...   
2      0.400000      0.490000      0.250000      0.350000      0.461538  ...   
3      0.466667      0.642857      0.558824      0.502370      0.555556  ...   

   raPlayerChampion  rsPlayerChampion  bCoopPlayer  rCoopPlayer  \
1          0.532043          0.528018    12.022353    10.448970   
2          0.495007          0.533597     9.449351     7.197822   
3          0.495007          0.533844     9.736232     8.088803   

   bCoopChampion  rCoopChampion   vsPlayer  vsChampion  bTeamColor  rTeamColor  
1       9.619471      11.370757  17.973818   15.762498    0.647059    0.568182  
2       8.599307      10.328071   2.111111   14.630073    0.405405    0.433962  
3      10.292419       9.165966  19.965797   17.989113    0.380952    0.522727  

[3 rows x 29 columns]

In [66]:
scaled_train = final_train.copy(deep=True)
for column in scaled_train.columns:
    if column != 'bResult':
        scaled_train[column] = (scaled_train[column] - scaled_train[column].mean()) / scaled_train[column].std()

In [68]:
scaled_train.head(3)

bResult  btPlayerRole  bjPlayerRole  bmPlayerRole  baPlayerRole  \
1      1.0      0.701884     -0.205048      0.975121      0.714486   
2      0.0     -0.233737     -0.483903     -0.007889     -0.728082   
3      1.0     -0.795546     -0.009849      0.719975     -0.010759   

   bsPlayerRole  rtPlayerRole  rjPlayerRole  rmPlayerRole  raPlayerRole  ...  \
1      0.685246     -0.001432      0.401764     -0.109146      0.472371  ...   
2     -0.667611     -0.052322     -1.655595     -0.996363     -0.249744  ...   
3     -0.228221      0.993817      0.401764      0.023766      0.386875  ...   

   raPlayerChampion  rsPlayerChampion  bCoopPlayer  rCoopPlayer  \
1          0.935151          0.706502     0.591416     0.150967   
2         -0.138737          0.847053    -0.181804    -0.824227   
3         -0.138737          0.853285    -0.095593    -0.556974   

   bCoopChampion  rCoopChampion  vsPlayer  vsChampion  bTeamColor  rTeamColor  
1      -0.427561       1.361532  0.282831    0.413140    1.050299    0.494876  
2      -1.419230       0.368822 -1.585880   -0.253838   -0.687879   -0.464691  
3       0.226590      -0.737584  0.517496    1.724576   -0.863766    0.169911  

[3 rows x 29 columns]

In [70]:
scaled_train.to_csv('trial_train_data2.csv')

In [72]:
# now do everything above with the test data
test_df = pd.DataFrame(data=imputed_test, columns=list(factorized_test.columns))

In [74]:
test_col_types = {}
for col in list(test_df.columns):
    test_col_types[col] = 'object'
test_df = test_df.astype(test_col_types)

In [76]:
for col in list(test_df.columns):
    col_name = col[11:]
    if col_name in test_imputation_index.keys():
        for index in range(len(test_imputation_index[col_name])):
            replacement_val = test_imputation_index[col_name][index]
            test_df.loc[test_df[col] == index, col] = replacement_val

In [92]:
def createPlayerRoleTest(col_name, col_alt, player, b_win):
    matches = len(list(test_df[test_df[col_name] == player][col_name]))
    matches += len(list(test_df[test_df[col_alt] == player][col_alt]))
    wins = len(list(test_df[(test_df[col_name] == player) & (test_df['bResult'] == b_win)][col_name]))
    wins += len(list(test_df[(test_df[col_alt] == player) & (test_df['bResult'] == switch(b_win))][col_alt]))
    if matches == 0:
        return 0.5
    else:
        return wins / matches

In [80]:
def createCoopPlayersTest(players, blue_cols, red_cols, b_win):
    total = 0
    for i in range(len(players)):
        sub_total = 0
        df_blue = test_df[(test_df[blue_cols[0]] == players[i]) | (test_df[blue_cols[1]] == players[i]) | \
        (test_df[blue_cols[2]] == players[i]) | (test_df[blue_cols[3]] == players[i]) | \
        (test_df[blue_cols[4]] == players[i])]
        df_red = test_df[(test_df[red_cols[0]] == players[i]) | (test_df[red_cols[1]] == players[i]) | \
        (test_df[red_cols[2]] == players[i]) | (test_df[red_cols[3]] == players[i]) | \
        (test_df[red_cols[4]] == players[i])]
        for j in range(len(players)):
            if i != j:
                # matches = len(list(train_df[(train_df[color_cols[i]] == players[i]) & (train_df[color_cols[j] == players[j])]))
                # wins = len(list(train_df[(train_df[color_cols[i]] == players[i]) & (train_df[color_cols[j] == players[j]) & \
                #                 (train_df['bResult'] == b_win)]))
                # ratio = wins / matches
                # sub_total += ratio
                matches = len(df_blue[(df_blue[blue_cols[0]] == players[j]) | (df_blue[blue_cols[1]] == players[j]) | \
                (df_blue[blue_cols[2]] == players[j]) | (df_blue[blue_cols[3]] == players[j]) | \
                (df_blue[blue_cols[4]] == players[j])])
                
                matches += len(df_red[(df_red[red_cols[0]] == players[j]) | (df_red[red_cols[1]] == players[j]) | \
                (df_red[red_cols[2]] == players[j]) | (df_red[red_cols[3]] == players[j]) | \
                (df_red[red_cols[4]] == players[j])])
                
                wins = len(df_blue[((df_blue[blue_cols[0]] == players[j]) | (df_blue[blue_cols[1]] == players[j]) | \
                (df_blue[blue_cols[2]] == players[j]) | (df_blue[blue_cols[3]] == players[j]) | \
                (df_blue[blue_cols[4]] == players[j])) & (df_blue['bResult'] == 1)])
                
                wins += len(df_red[((df_red[red_cols[0]] == players[j]) | (df_red[red_cols[1]] == players[j]) | \
                (df_red[red_cols[2]] == players[j]) | (df_red[red_cols[3]] == players[j]) | \
                (df_red[red_cols[4]] == players[j])) & (df_red['bResult'] == 0)])
                ratio = 0
                if matches == 0:
                    ratio += 0.5
                else:
                    ratio += wins / matches
                sub_total += ratio
        total += sub_total
    return total

In [82]:
def createVSPlayerTest(blue_players, red_players, blue_cols, red_cols):
    total = 0
    for bp in blue_players:
        sub_total = 0
        df_blue = test_df[(test_df[blue_cols[0]] == bp) | (test_df[blue_cols[1]] == bp) | \
        (test_df[blue_cols[2]] == bp) | (test_df[blue_cols[3]] == bp) | \
        (test_df[blue_cols[4]] == bp)]
        df_red = test_df[(test_df[red_cols[0]] == bp) | (test_df[red_cols[1]] == bp) | \
        (test_df[red_cols[2]] == bp) | (test_df[red_cols[3]] == bp) | \
        (test_df[red_cols[4]] == bp)]
        for rp in red_players:
            matches = len(df_blue[(df_blue[red_cols[0]] == bp) | (df_blue[red_cols[1]] == rp) | \
                (df_blue[red_cols[2]] == rp) | (df_blue[red_cols[3]] == rp) | \
                (df_blue[red_cols[4]] == rp)])
            matches += len(df_red[(df_red[blue_cols[0]] == rp) | (df_red[blue_cols[1]] == rp) | \
                (df_red[blue_cols[2]] == rp) | (df_red[blue_cols[3]] == rp) | \
                (df_red[blue_cols[4]] == rp)])
            wins = len(df_blue[((df_blue[red_cols[0]] == rp) | (df_blue[red_cols[1]] == rp) | \
                (df_blue[red_cols[2]] == rp) | (df_blue[red_cols[3]] == rp) | \
                (df_blue[red_cols[4]] == rp)) & (df_blue['bResult'] == 1)])
            wins += len(df_red[((df_red[blue_cols[0]] == rp) | (df_red[blue_cols[1]] == rp) | \
                (df_red[blue_cols[2]] == rp) | (df_red[blue_cols[3]] == rp) | \
                (df_red[blue_cols[4]] == rp)) & (df_red['bResult'] == 0)])
            ratio = 0
            if matches == 0:
                ratio += 0.5
            else:
                ratio += wins / matches
            sub_total += ratio
        total += sub_total
    return total

In [90]:
def createTeamColorTest(team_tag):
    matches = len(test_df[test_df['factorized_blueTeamTag'] == team_tag])
    matches += len(test_df[test_df['factorized_redTeamTag'] == team_tag])
    
    wins = len(test_df[(test_df['factorized_blueTeamTag'] == team_tag) & (test_df['bResult'] == 1)])
    wins += len(test_df[(test_df['factorized_redTeamTag'] == team_tag) & (test_df['bResult'] == 0)])
    
    if matches == 0:
        return 0.5
    else:
        return wins / matches

In [94]:
# need to add this first row because cannot append the other rows to an empty dataframe
final_test = pd.DataFrame(data=[[0, 0, 0, 0, 0, 0, \
                                 0, 0, 0, 0, 0, 0, \
                                 0, 0, 0, 0, 0, \
                                 0, 0, 0, 0, 0, 0, \
                                 0, 0, 0, 0, 0, 0]], columns=new_cols)

In [96]:
for index, row in test_df.iterrows():
# btPlayerRole
    bt_player = row['factorized_blueTop']
    bt_player_role = createPlayerRole(player_roles['top'][0], player_roles['top'][1], bt_player, 1)
# bjPlayerRole
    bj_player = row['factorized_blueJungle']
    bj_player_role = createPlayerRole(player_roles['jungle'][0], player_roles['jungle'][1], bj_player, 1)
# bmPlayerRole
    bm_player = row['factorized_blueMiddle']
    bm_player_role = createPlayerRole(player_roles['middle'][0], player_roles['middle'][1], bm_player, 1)
# baPlayerRole
    ba_player = row['factorized_blueADC']
    ba_player_role = createPlayerRole(player_roles['adc'][0], player_roles['adc'][1], ba_player, 1)
# bsPlayerRole
    bs_player = row['factorized_blueSupport']
    bs_player_role = createPlayerRole(player_roles['support'][0], player_roles['support'][1], bs_player, 1)
# rtPlayerRole
    rt_player = row['factorized_redTop']
    rt_player_role = createPlayerRole(player_roles['top'][1], player_roles['top'][0], rt_player, 0)
# rjPlayerRole
    rj_player = row['factorized_redJungle']
    rj_player_role = createPlayerRole(player_roles['jungle'][1], player_roles['jungle'][0], rj_player, 0)
# rmPlayerRole
    rm_player = row['factorized_redMiddle']
    rm_player_role = createPlayerRole(player_roles['middle'][1], player_roles['middle'][0], rm_player, 0)
# raPlayerRole
    ra_player = row['factorized_redADC']
    ra_player_role = createPlayerRole(player_roles['adc'][1], player_roles['adc'][0], ra_player, 0)
# rsPlayerRole
    rs_player = row['factorized_redSupport']
    rs_player_role = createPlayerRole(player_roles['support'][1], player_roles['support'][0], rs_player, 0)
# btPlayerChampion
    bt_champ = row['factorized_blueTopChamp']
    bt_player_champion = createPlayerRole(champ_roles['top'][0], champ_roles['top'][1], bt_champ, 1)
# bjPlayerChampion
    bj_champ = row['factorized_blueJungleChamp']
    bj_player_champion = createPlayerRole(champ_roles['jungle'][0], champ_roles['jungle'][1], bj_champ, 1)
# bmPlayerChampion
    bm_champ = row['factorized_blueMiddleChamp']
    bm_player_champion = createPlayerRole(champ_roles['middle'][0], champ_roles['middle'][1], bm_champ, 1)
# baPlayerChampion
    ba_champ = row['factorized_blueADCChamp']
    ba_player_champion = createPlayerRole(champ_roles['adc'][0], champ_roles['adc'][1], ba_champ, 1)
# bsPlayerChampion
    bs_champ = row['factorized_blueSupportChamp']
    bs_player_champion = createPlayerRole(champ_roles['support'][0], champ_roles['support'][1], bs_champ, 1)
# rtPlayerChampion
    rt_champ = row['factorized_redTopChamp']
    rt_player_champion = createPlayerRole(champ_roles['top'][1], champ_roles['top'][0], rt_champ, 0)
# rjPlayerChampion
    rj_champ = row['factorized_redJungleChamp']
    rj_player_champion = createPlayerRole(champ_roles['jungle'][1], champ_roles['jungle'][0], rj_champ, 0)
# rmPlayerChampion
    rm_champ = row['factorized_redMiddleChamp']
    rm_player_champion = createPlayerRole(champ_roles['middle'][1], champ_roles['middle'][0], rm_champ, 0)
# raPlayerChampion
    ra_champ = row['factorized_redADCChamp']
    ra_player_champion = createPlayerRole(champ_roles['adc'][1], champ_roles['adc'][0], ra_champ, 0)
# rsPlayerChampion
    rs_champ = row['factorized_redSupportChamp']
    rs_player_champion = createPlayerRole(champ_roles['support'][1], champ_roles['support'][0], rs_champ, 0)
# bCoopPlayer
    blue_players = [bt_player, bj_player, bm_player, ba_player, bs_player]
    blue_cols = ['factorized_blueTop', 'factorized_blueJungle', 'factorized_blueMiddle', 'factorized_blueADC', 'factorized_blueSupport']
    red_cols = ['factorized_redTop', 'factorized_redJungle', 'factorized_redMiddle', 'factorized_redADC', 'factorized_redSupport']
    b_coop_player = createCoopPlayers(blue_players, blue_cols, red_cols, 1)
# rCoopPlayer
    red_players = [rt_player, rj_player, rm_player, ra_player, rs_player]
    r_coop_player = createCoopPlayers(red_players, blue_cols, red_cols, 0)
# bCoopChampion
    blue_champs = [bt_champ, bj_champ, bm_champ, ba_champ, bs_champ]
    blue_champ_cols = ['factorized_blueTopChamp', 'factorized_blueJungleChamp', 'factorized_blueMiddleChamp', 'factorized_blueADCChamp', \
                 'factorized_blueSupportChamp']
    red_champ_cols = ['factorized_redTopChamp', 'factorized_redJungleChamp', 'factorized_redMiddleChamp', 'factorized_redADCChamp', \
                 'factorized_redSupportChamp']
    b_coop_champion = createCoopPlayers(blue_champs, blue_champ_cols, red_champ_cols, 1)
# rCoopChampion
    red_champs = [rt_champ, rj_champ, rm_champ, ra_champ, rs_champ]
    r_coop_champion = createCoopPlayers(red_champs, blue_champ_cols, red_champ_cols, 0)
# vsPlayer
    vs_player = createVSPlayer(blue_players, red_players, blue_cols, red_cols)
# vsChampion
    vs_champion = createVSPlayer(blue_champs, red_champs, blue_champ_cols, red_champ_cols)
# bTeamColor
    # b_team_color = createTeamColor(blue_players + blue_champs, blue_cols + blue_champ_cols, 1)
    b_team_tag = row['factorized_blueTeamTag']
    b_team_color = createTeamColor(b_team_tag)
# rTeamColor
    # r_team_color = createTeamColor(red_players + red_champs, red_cols + red_champ_cols, 0)
    r_team_tag = row['factorized_redTeamTag']
    r_team_color = createTeamColor(r_team_tag)
    new_col_values = [row['bResult'], bt_player_role, bj_player_role, bm_player_role, ba_player_role, bs_player_role, \
                     rt_player_role, rj_player_role, rm_player_role, ra_player_role, rs_player_role, \
                     bt_player_champion, bj_player_champion, bm_player_champion, ba_player_champion, bs_player_champion, \
                     rt_player_champion, rj_player_champion, rm_player_champion, ra_player_champion, rs_player_champion, \
                     b_coop_player, r_coop_player, b_coop_champion, r_coop_champion, vs_player, vs_champion, b_team_color, \
                     r_team_color]
    new_row = {}
    for new_col in range(len(new_col_values)):
        new_row[new_cols[new_col]] = new_col_values[new_col]
    print(new_row)
    final_test = final_test._append(new_row, ignore_index=True)

{'bResult': 1.0, 'btPlayerRole': 0.544, 'bjPlayerRole': 0.5603112840466926, 'bmPlayerRole': 0.6088888888888889, 'baPlayerRole': 0.5619047619047619, 'bsPlayerRole': 0.5515695067264574, 'rtPlayerRole': 0.5543859649122806, 'rjPlayerRole': 0.5573770491803278, 'rmPlayerRole': 0.5023696682464455, 'raPlayerRole': 0.5, 'rsPlayerRole': 0.6190476190476191, 'btPlayerChampion': 0.49471830985915494, 'bjPlayerChampion': 0.4899951195705222, 'bmPlayerChampion': 0.5181268882175226, 'baPlayerChampion': 0.49331550802139035, 'bsPlayerChampion': 0.5159663865546219, 'rtPlayerChampion': 0.5458937198067633, 'rjPlayerChampion': 0.4961832061068702, 'rmPlayerChampion': 0.5, 'raPlayerChampion': 0.5320427236315087, 'rsPlayerChampion': 0.5338441890166028, 'bCoopPlayer': 11.518234787389119, 'rCoopPlayer': 9.718938790931778, 'bCoopChampion': 10.615976063046794, 'rCoopChampion': 9.930035038208832, 'vsPlayer': 9.99797619047619, 'vsChampion': 14.851695496482654, 'bTeamColor': 0.627906976744186, 'rTeamColor': 0.433962264

In [98]:
final_test.head(3)

bResult  btPlayerRole  bjPlayerRole  bmPlayerRole  baPlayerRole  \
0      0.0      0.000000      0.000000      0.000000      0.000000   
1      1.0      0.544000      0.560311      0.608889      0.561905   
2      0.0      0.578231      0.630996      0.611940      0.489362   

   bsPlayerRole  rtPlayerRole  rjPlayerRole  rmPlayerRole  raPlayerRole  ...  \
0      0.000000      0.000000      0.000000      0.000000      0.000000  ...   
1      0.551570      0.554386      0.557377      0.502370      0.500000  ...   
2      0.486667      0.438095      0.696078      0.707692      0.721448  ...   

   raPlayerChampion  rsPlayerChampion  bCoopPlayer  rCoopPlayer  \
0          0.000000          0.000000     0.000000     0.000000   
1          0.532043          0.533844    11.518235     9.718939   
2          0.553082          0.507692    11.117927    13.617495   

   bCoopChampion  rCoopChampion   vsPlayer  vsChampion  bTeamColor  rTeamColor  
0       0.000000       0.000000   0.000000    0.000000    0.000000    0.000000  
1      10.615976       9.930035   9.997976   14.851695    0.627907    0.433962  
2      10.705702      10.540845  13.400063   15.629553    0.578767    0.721448  

[3 rows x 29 columns]

In [100]:
# dropping that first row of zeros
final_test = final_test.drop(0)
final_test.head(3)

bResult  btPlayerRole  bjPlayerRole  bmPlayerRole  baPlayerRole  \
1      1.0      0.544000      0.560311      0.608889      0.561905   
2      0.0      0.578231      0.630996      0.611940      0.489362   
3      0.0      0.340000      0.478632      0.637931      0.500000   

   bsPlayerRole  rtPlayerRole  rjPlayerRole  rmPlayerRole  raPlayerRole  ...  \
1      0.551570      0.554386      0.557377      0.502370      0.500000  ...   
2      0.486667      0.438095      0.696078      0.707692      0.721448  ...   
3      0.388889      0.346939      0.346939      0.333333      0.450000  ...   

   raPlayerChampion  rsPlayerChampion  bCoopPlayer  rCoopPlayer  \
1          0.532043          0.533844    11.518235     9.718939   
2          0.553082          0.507692    11.117927    13.617495   
3          0.474348          0.481127    10.000000    12.206698   

   bCoopChampion  rCoopChampion   vsPlayer  vsChampion  bTeamColor  rTeamColor  
1      10.615976       9.930035   9.997976   14.851695    0.627907    0.433962  
2      10.705702      10.540845  13.400063   15.629553    0.578767    0.721448  
3       8.655336      10.026757  13.846825   15.416812    0.601695    0.666667  

[3 rows x 29 columns]

In [102]:
# z-score normalization
scaled_test = final_test.copy(deep=True)
for column in scaled_test.columns:
    if column != 'bResult':
        scaled_test[column] = (scaled_test[column] - scaled_test[column].mean()) / scaled_test[column].std()

In [104]:
scaled_test.head(3)

bResult  btPlayerRole  bjPlayerRole  bmPlayerRole  baPlayerRole  \
1      1.0      0.322360      0.405608      0.733284      0.442528   
2      0.0      0.565264      0.870173      0.754311     -0.042977   
3      0.0     -1.125216     -0.131212      0.933416      0.028221   

   bsPlayerRole  rtPlayerRole  rjPlayerRole  rmPlayerRole  raPlayerRole  ...  \
1      0.353438      0.341565      0.353684     -0.001304     -0.028535  ...   
2     -0.082623     -0.444803      1.266457      1.377068      1.505800  ...   
3     -0.739561     -1.061211     -1.031180     -1.136079     -0.374966  ...   

   raPlayerChampion  rsPlayerChampion  bCoopPlayer  rCoopPlayer  \
1          1.054245          0.864355     0.473506    -0.100604   
2          1.790540          0.214260     0.351443     1.067221   
3         -0.964826         -0.446111     0.010562     0.644612   

   bCoopChampion  rCoopChampion  vsPlayer  vsChampion  bTeamColor  rTeamColor  
1       0.708277      -0.070203 -0.532266    0.026327    0.862385   -0.465940  
2       0.814504       0.715313 -0.109838    0.555813    0.516987    1.613979  
3      -1.612945       0.054185 -0.054364    0.411001    0.678144    1.217641  

[3 rows x 29 columns]

In [106]:
scaled_test.to_csv('trial_test_data2.csv')

In [ ]:
def createPlayerRole(col_name, col_alt, player, b_win, df):
    matches = len(list(df[df[col_name] == player][col_name]))
    matches += len(list(df[df[col_alt] == player][col_alt]))
    wins = len(list(df[(df[col_name] == player) & (df['bResult'] == b_win)][col_name]))
    wins += len(list(df[(df[col_alt] == player) & (df['bResult'] == switch(b_win))][col_alt]))
    if matches == 0:
        return 0.5
    else:
        return wins / matches

In [ ]:
def createCoopPlayers(players, blue_cols, red_cols, b_win, df):
    total = 0
    for i in range(len(players)):
        sub_total = 0
        df_blue = df[(df[blue_cols[0]] == players[i]) | (df[blue_cols[1]] == players[i]) | \
        (df[blue_cols[2]] == players[i]) | (df[blue_cols[3]] == players[i]) | \
        (df[blue_cols[4]] == players[i])]
        df_red = df[(df[red_cols[0]] == players[i]) | (df[red_cols[1]] == players[i]) | \
        (df[red_cols[2]] == players[i]) | (df[red_cols[3]] == players[i]) | \
        (df[red_cols[4]] == players[i])]
        for j in range(len(players)):
            if i != j:
                # matches = len(list(train_df[(train_df[color_cols[i]] == players[i]) & (train_df[color_cols[j] == players[j])]))
                # wins = len(list(train_df[(train_df[color_cols[i]] == players[i]) & (train_df[color_cols[j] == players[j]) & \
                #                 (train_df['bResult'] == b_win)]))
                # ratio = wins / matches
                # sub_total += ratio
                matches = len(df_blue[(df_blue[blue_cols[0]] == players[j]) | (df_blue[blue_cols[1]] == players[j]) | \
                (df_blue[blue_cols[2]] == players[j]) | (df_blue[blue_cols[3]] == players[j]) | \
                (df_blue[blue_cols[4]] == players[j])])
                
                matches += len(df_red[(df_red[red_cols[0]] == players[j]) | (df_red[red_cols[1]] == players[j]) | \
                (df_red[red_cols[2]] == players[j]) | (df_red[red_cols[3]] == players[j]) | \
                (df_red[red_cols[4]] == players[j])])
                
                wins = len(df_blue[((df_blue[blue_cols[0]] == players[j]) | (df_blue[blue_cols[1]] == players[j]) | \
                (df_blue[blue_cols[2]] == players[j]) | (df_blue[blue_cols[3]] == players[j]) | \
                (df_blue[blue_cols[4]] == players[j])) & (df_blue['bResult'] == 1)])
                
                wins += len(df_red[((df_red[red_cols[0]] == players[j]) | (df_red[red_cols[1]] == players[j]) | \
                (df_red[red_cols[2]] == players[j]) | (df_red[red_cols[3]] == players[j]) | \
                (df_red[red_cols[4]] == players[j])) & (df_red['bResult'] == 0)])
                ratio = 0
                if matches == 0:
                    ratio += 0.5
                else:
                    ratio += wins / matches
                sub_total += ratio
        total += sub_total
    return total

In [ ]:
def createVSPlayer(blue_players, red_players, blue_cols, red_cols, df):
    total = 0
    for bp in blue_players:
        sub_total = 0
        df_blue = df[(df[blue_cols[0]] == bp) | (df[blue_cols[1]] == bp) | \
        (df[blue_cols[2]] == bp) | (df[blue_cols[3]] == bp) | \
        (df[blue_cols[4]] == bp)]
        df_red = df[(df[red_cols[0]] == bp) | (df[red_cols[1]] == bp) | \
        (df[red_cols[2]] == bp) | (df[red_cols[3]] == bp) | \
        (df[red_cols[4]] == bp)]
        for rp in red_players:
            matches = len(df_blue[(df_blue[red_cols[0]] == bp) | (df_blue[red_cols[1]] == rp) | \
                (df_blue[red_cols[2]] == rp) | (df_blue[red_cols[3]] == rp) | \
                (df_blue[red_cols[4]] == rp)])
            matches += len(df_red[(df_red[blue_cols[0]] == rp) | (df_red[blue_cols[1]] == rp) | \
                (df_red[blue_cols[2]] == rp) | (df_red[blue_cols[3]] == rp) | \
                (df_red[blue_cols[4]] == rp)])
            wins = len(df_blue[((df_blue[red_cols[0]] == rp) | (df_blue[red_cols[1]] == rp) | \
                (df_blue[red_cols[2]] == rp) | (df_blue[red_cols[3]] == rp) | \
                (df_blue[red_cols[4]] == rp)) & (df_blue['bResult'] == 1)])
            wins += len(df_red[((df_red[blue_cols[0]] == rp) | (df_red[blue_cols[1]] == rp) | \
                (df_red[blue_cols[2]] == rp) | (df_red[blue_cols[3]] == rp) | \
                (df_red[blue_cols[4]] == rp)) & (df_red['bResult'] == 0)])
            ratio = 0
            if matches == 0:
                ratio += 0.5
            else:
                ratio += wins / matches
            sub_total += ratio
        total += sub_total
    return total

In [ ]:
def createTeamColor(team_tag, df):
    matches = len(df[df['factorized_blueTeamTag'] == team_tag])
    matches += len(df[df['factorized_redTeamTag'] == team_tag])
    
    wins = len(df[(df['factorized_blueTeamTag'] == team_tag) & (df['bResult'] == 1)])
    wins += len(df[(df['factorized_redTeamTag'] == team_tag) & (df['bResult'] == 0)])
    
    if matches == 0:
        return 0.5
    else:
        return wins / matches

In [ ]:
def createFinalDF(df):
    final_df = pd.DataFrame(data=[[0, 0, 0, 0, 0, 0, \
                                 0, 0, 0, 0, 0, 0, \
                                 0, 0, 0, 0, 0, \
                                 0, 0, 0, 0, 0, 0, \
                                 0, 0, 0, 0, 0, 0]], columns=new_cols)
    for index, row in df.iterrows():
# btPlayerRole
        bt_player = row['factorized_blueTop']
        bt_player_role = createPlayerRole(player_roles['top'][0], player_roles['top'][1], bt_player, 1)
# bjPlayerRole
        bj_player = row['factorized_blueJungle']
        bj_player_role = createPlayerRole(player_roles['jungle'][0], player_roles['jungle'][1], bj_player, 1)
# bmPlayerRole
        bm_player = row['factorized_blueMiddle']
        bm_player_role = createPlayerRole(player_roles['middle'][0], player_roles['middle'][1], bm_player, 1)
# baPlayerRole
        ba_player = row['factorized_blueADC']
        ba_player_role = createPlayerRole(player_roles['adc'][0], player_roles['adc'][1], ba_player, 1)
# bsPlayerRole
        bs_player = row['factorized_blueSupport']
        bs_player_role = createPlayerRole(player_roles['support'][0], player_roles['support'][1], bs_player, 1)
# rtPlayerRole
        rt_player = row['factorized_redTop']
        rt_player_role = createPlayerRole(player_roles['top'][1], player_roles['top'][0], rt_player, 0)
# rjPlayerRole
        rj_player = row['factorized_redJungle']
        rj_player_role = createPlayerRole(player_roles['jungle'][1], player_roles['jungle'][0], rj_player, 0)
# rmPlayerRole
        rm_player = row['factorized_redMiddle']
        rm_player_role = createPlayerRole(player_roles['middle'][1], player_roles['middle'][0], rm_player, 0)
# raPlayerRole
        ra_player = row['factorized_redADC']
        ra_player_role = createPlayerRole(player_roles['adc'][1], player_roles['adc'][0], ra_player, 0)
# rsPlayerRole
        rs_player = row['factorized_redSupport']
        rs_player_role = createPlayerRole(player_roles['support'][1], player_roles['support'][0], rs_player, 0)
# btPlayerChampion
        bt_champ = row['factorized_blueTopChamp']
        bt_player_champion = createPlayerRole(champ_roles['top'][0], champ_roles['top'][1], bt_champ, 1)
# bjPlayerChampion
        bj_champ = row['factorized_blueJungleChamp']
        bj_player_champion = createPlayerRole(champ_roles['jungle'][0], champ_roles['jungle'][1], bj_champ, 1)
# bmPlayerChampion
        bm_champ = row['factorized_blueMiddleChamp']
        bm_player_champion = createPlayerRole(champ_roles['middle'][0], champ_roles['middle'][1], bm_champ, 1)
# baPlayerChampion
        ba_champ = row['factorized_blueADCChamp']
        ba_player_champion = createPlayerRole(champ_roles['adc'][0], champ_roles['adc'][1], ba_champ, 1)
# bsPlayerChampion
        bs_champ = row['factorized_blueSupportChamp']
        bs_player_champion = createPlayerRole(champ_roles['support'][0], champ_roles['support'][1], bs_champ, 1)
# rtPlayerChampion
        rt_champ = row['factorized_redTopChamp']
        rt_player_champion = createPlayerRole(champ_roles['top'][1], champ_roles['top'][0], rt_champ, 0)
# rjPlayerChampion
        rj_champ = row['factorized_redJungleChamp']
        rj_player_champion = createPlayerRole(champ_roles['jungle'][1], champ_roles['jungle'][0], rj_champ, 0)
# rmPlayerChampion
        rm_champ = row['factorized_redMiddleChamp']
        rm_player_champion = createPlayerRole(champ_roles['middle'][1], champ_roles['middle'][0], rm_champ, 0)
# raPlayerChampion
        ra_champ = row['factorized_redADCChamp']
        ra_player_champion = createPlayerRole(champ_roles['adc'][1], champ_roles['adc'][0], ra_champ, 0)
# rsPlayerChampion
        rs_champ = row['factorized_redSupportChamp']
        rs_player_champion = createPlayerRole(champ_roles['support'][1], champ_roles['support'][0], rs_champ, 0)
# bCoopPlayer
        blue_players = [bt_player, bj_player, bm_player, ba_player, bs_player]
        blue_cols = ['factorized_blueTop', 'factorized_blueJungle', 'factorized_blueMiddle', 'factorized_blueADC', 'factorized_blueSupport']
        red_cols = ['factorized_redTop', 'factorized_redJungle', 'factorized_redMiddle', 'factorized_redADC', 'factorized_redSupport']
        b_coop_player = createCoopPlayers(blue_players, blue_cols, red_cols, 1)
# rCoopPlayer
        red_players = [rt_player, rj_player, rm_player, ra_player, rs_player]
        r_coop_player = createCoopPlayers(red_players, blue_cols, red_cols, 0)
# bCoopChampion
        blue_champs = [bt_champ, bj_champ, bm_champ, ba_champ, bs_champ]
        blue_champ_cols = ['factorized_blueTopChamp', 'factorized_blueJungleChamp', 'factorized_blueMiddleChamp', 'factorized_blueADCChamp', \
                     'factorized_blueSupportChamp']
        red_champ_cols = ['factorized_redTopChamp', 'factorized_redJungleChamp', 'factorized_redMiddleChamp', 'factorized_redADCChamp', \
                     'factorized_redSupportChamp']
        b_coop_champion = createCoopPlayers(blue_champs, blue_champ_cols, red_champ_cols, 1)
# rCoopChampion
        red_champs = [rt_champ, rj_champ, rm_champ, ra_champ, rs_champ]
        r_coop_champion = createCoopPlayers(red_champs, blue_champ_cols, red_champ_cols, 0)
# vsPlayer
        vs_player = createVSPlayer(blue_players, red_players, blue_cols, red_cols)
# vsChampion
        vs_champion = createVSPlayer(blue_champs, red_champs, blue_champ_cols, red_champ_cols)
# bTeamColor
    # b_team_color = createTeamColor(blue_players + blue_champs, blue_cols + blue_champ_cols, 1)
        b_team_tag = row['factorized_blueTeamTag']
        b_team_color = createTeamColor(b_team_tag)
# rTeamColor
    # r_team_color = createTeamColor(red_players + red_champs, red_cols + red_champ_cols, 0)
        r_team_tag = row['factorized_redTeamTag']
        r_team_color = createTeamColor(r_team_tag)
        new_col_values = [row['bResult'], bt_player_role, bj_player_role, bm_player_role, ba_player_role, bs_player_role, \
                         rt_player_role, rj_player_role, rm_player_role, ra_player_role, rs_player_role, \
                         bt_player_champion, bj_player_champion, bm_player_champion, ba_player_champion, bs_player_champion, \
                         rt_player_champion, rj_player_champion, rm_player_champion, ra_player_champion, rs_player_champion, \
                         b_coop_player, r_coop_player, b_coop_champion, r_coop_champion, vs_player, vs_champion, b_team_color, \
                         r_team_color]
        new_row = {}
        for new_col in range(len(new_col_values)):
            new_row[new_cols[new_col]] = new_col_values[new_col]
        print(new_row)
        final_df = final_df._append(new_row, ignore_index=True)
    return final_df

In [ ]:
# performs preprocessing steps
# input: pandas dataframe, filename for the name of the csv file that the processed dataframe should be saved to
def processDF(df, filename):
    imputer = KNNImputer(n_neighbors=5)
    factorized_cols = {}
    df = df.drop(['index', 'League', 'Year', 'Season', 'Type', 'Address', 'Unnamed: 31', 'gamelength'], axis=1)
    need_factorizing = list(df.columns)
    need_factorizing.pop(1)
    need_factorizing.pop(1)
    imputation_index = {}
    for col in need_factorizing:
        factorization = pd.factorize(df[col])
        factorized_cols[col] = factorization[0]
        imputation_index[col] = list(factorization[1])
    factorized_df = df[['bResult', 'rResult']].copy(deep=True)
    for col in need_factorizing:
        col_name = 'factorized_' + col
        factorized_df[col_name] = factorized_cols[col]
    imputed_df = imputer.fit_transform(factorized_df)
    prepped_df = pd.DataFrame(data=imputed_df, columns=list(factorized_df.columns))
    col_types = {}
    for col in list(prepped_df.columns):
        col_types[col] = 'object'
    prepped_df = prepped_df.astype(col_types)
    for col in list(prepped_df.columns):
        col_name = col[11:]
    if col_name in imputation_index.keys():
        for index in range(len(imputation_index[col_name])):
            replacement_val = imputation_index[col_name][index]
            prepped_df.loc[prepped_df[col] == index, col] = replacement_val
    final_df = createFinalDF(prepped_df)
    final_df = final_df.drop(0)
    scaled_df = final_df.copy(deep=True)
    for column in scaled_df.columns:
        if column != 'bResult':
            scaled_df[column] = (scaled_df[column] - scaled_df[column].mean()) / scaled_df[column].std()
    scaled_train.to_csv(filename)